In [ ]:
import os
import numpy as np
import pandas as pd
import rdkit
from rdkit import Chem
from rdkit.Chem import Descriptors

from rdkit import RDLogger
RDLogger.DisableLog('rdApp.*')

In [ ]:
bool_saved = True

In [206]:
folderName_results = "../s2_runfSepaMolGen/results_AmEu/"
folderName2_results = "results202508101432_GPT5_SMILES10x10" # Change folder name
folderPath_results = os.path.join(folderName_results, folderName2_results)

if bool_saved:
    folderName_saved = "results_AmEu_proc"
    folderPath_saved = os.path.join(folderName_saved, folderName2_results, 'structures')
    os.makedirs(folderPath_saved, exist_ok=True)

In [207]:
fileName_genSMILESeval = "genSMILESeval.xlsx"
filePath_genSMILESeval = os.path.join(folderPath_results, fileName_genSMILESeval)

df_genSMILESeval = pd.read_excel(filePath_genSMILESeval)
df_genSMILESeval.head(1)

Gen_SMILES    Target_metal  \
0  n1cc(-c2nnc(C(C)(C)C)c(C(C)(C)C)n2)ccc1-c3ccc(...  Invalid SMILES   

      Other_metal         Source Similarity_to_Experimental  \
0  Invalid SMILES  LLM generated             Invalid SMILES   

  Similarity_to_Generated            LogP  
0          Invalid SMILES  Invalid SMILES

In [208]:
def calc_complexity_score(smiles):
    m = Chem.MolFromSmiles(smiles)
    if m:
        complexity_score = Descriptors.BertzCT(m)
    else:
        complexity_score = 0
    return complexity_score

df_genSMILESeval['BertzCT'] = df_genSMILESeval['Gen_SMILES'].apply(calc_complexity_score)
print(df_genSMILESeval.shape)
df_genSMILESeval.head(2)

(100, 8)


Gen_SMILES    Target_metal  \
0  n1cc(-c2nnc(C(C)(C)C)c(C(C)(C)C)n2)ccc1-c3ccc(...  Invalid SMILES   
1  n1cc(-c2nnc(CCC(CC)CC)c(CCC(CC)CC)n2)ccc1-c3cc...  Invalid SMILES   

      Other_metal         Source Similarity_to_Experimental  \
0  Invalid SMILES  LLM generated             Invalid SMILES   
1  Invalid SMILES  LLM generated             Invalid SMILES   

  Similarity_to_Generated            LogP  BertzCT  
0          Invalid SMILES  Invalid SMILES      0.0  
1          Invalid SMILES  Invalid SMILES      0.0

In [209]:
df_genSMILESeval_GoodMol = df_genSMILESeval[
    (df_genSMILESeval['Target_metal'] == 'ORGANIC') &
    (df_genSMILESeval['Other_metal'] == 'AQUEOUS') &
    ((df_genSMILESeval['Similarity_to_Experimental'] == 'MEDIUM') | (df_genSMILESeval['Similarity_to_Experimental'] == 'LOW')) &
    (df_genSMILESeval['Similarity_to_Generated'] != 'HIGH') &
    (df_genSMILESeval['LogP'] == 'ORGANIC')
][['Gen_SMILES', 'BertzCT']]

df_genSMILESeval_GoodMol['logBertzCT'] = round(np.log10(df_genSMILESeval_GoodMol['BertzCT']),2)

print(df_genSMILESeval_GoodMol.shape)
df_genSMILESeval_GoodMol.head(2)

(90, 3)


Gen_SMILES      BertzCT  logBertzCT
6  c1cc(-c2nnc(C(C)(C)CC(C)(C)C)c(C(C)(C)CC(C)(C)...  1516.605187        3.18
7  c1cc(-c2nnc(C1C2CC3CC(C2)CC1C3)c(C1C2CC3CC(C2)...  2130.129940        3.33

In [ ]:
if bool_saved:
    fileName_GoodMols= "GoodMols.xlsx"
    filePath_GoodMols = os.path.join(folderPath_saved, fileName_GoodMols)
    df_genSMILESeval_GoodMol.to_excel(filePath_GoodMols, index_label="Mol_ID")

In [ ]:
# Save clear bkg structures
if bool_saved:
    for i, row in df_genSMILESeval_GoodMol.iterrows():
        m = Chem.MolFromSmiles(row['Gen_SMILES'])
        
        drawer = Chem.Draw.rdMolDraw2D.MolDraw2DCairo(600, 600)
        opts = drawer.drawOptions()
        opts.clearBackground = False
        opts.cropMargins = True
        opts.bondLineWidth = 6
        Chem.Draw.rdMolDraw2D.PrepareAndDrawMolecule(drawer, m)
        drawer.FinishDrawing()
        
        logBertzCT = row['logBertzCT']
        list_cut = [2.4, 2.6, 2.8, 3.0, 3.2]
        sets = np.digitize(logBertzCT, list_cut)

        imageName_oneMol = f"set{sets}_mol{i}_logComp{logBertzCT}.png"
        imagePath_oneMol = os.path.join(folderPath_saved, imageName_oneMol)
        
        with open(imagePath_oneMol, "wb") as f:
            f.write(drawer.GetDrawingText())

In [ ]:
# Display and save grid structures
list_mol_obj = [Chem.MolFromSmiles(smile) for smile in df_genSMILESeval_GoodMol['Gen_SMILES']]
img = Chem.Draw.MolsToGridImage(
    list_mol_obj,
    molsPerRow=10,
    subImgSize=(800, 800),
    useSVG=False,
    returnPNG=False,
    maxMols=100
)

if bool_saved:
    imageName_grid = 'structures_grid.png'
    imagePath_grid = os.path.join(folderPath_saved, imageName_grid)
    img.save(imagePath_grid)

img